In [1]:
import folium
import pandas as pd
import numpy as np
import osmnx as ox
import networkx as nx
import matplotlib.pyplot as plt
import seaborn as sns
import branca.colormap as cmp

### Google API Key

In [1]:
google_elevation_api_key = r''
display(google_elevation_api_key)

''

# Pheonix Route From Karl


## Get Coordinate List

- Copy From Trace Route-Phoenix City
- There seems to be an issue in the top left
    - Not sure why Karl code doesn't have the same issue other than the shortest path algorithm had different results.
    - Not import for this route but is a bug that I'll need to write up since it doesn't change the functionality and probably isn't going to show up on the freeway route

In [3]:
phoenixCityCoords = [[33.465634, -112.056190],[33.465743, -112.063888],[33.465687, -112.075976],[33.469577, -112.075867],[33.469475, -112.073799],[33.465680, -112.073949],[33.451435, -112.075165],[33.451312, -112.065134],[33.447234, -112.065173],[33.447162, -112.057534],[33.447192, -112.047844],[33.427749, -112.047924],[33.427915, -112.053949],[33.4293304,-112.0651226],[33.4284678,-112.0651097],[33.427293, -112.042925],[33.4317373,-112.0373349],[33.4433703,-112.0371146],[33.4555424,-112.0365537],[33.461889, -112.037190],[33.465836, -112.039303],[33.465772, -112.044155],[33.465634, -112.056190]]

## OSMnx Graph and Route

### Find Bounding Box Points

In [4]:
# Calculate the north, south, east, and west coordinates
phoenixCityCoordsLats, phoenixCityCoordsLongs = zip(*phoenixCityCoords)
northern_lat = max(phoenixCityCoordsLats)
southern_lat = min(phoenixCityCoordsLats)
eastern_long = max(phoenixCityCoordsLongs)
western_long = min(phoenixCityCoordsLongs)

# display(phoenixCityCoordsLats, phoenixCityCoordsLongs)
display(northern_lat, western_long, southern_lat, eastern_long)

33.469577

-112.075976

33.427293

-112.0365537

### Create Graph with Bounding Box

In [5]:
# add buffer to bounding box
phoenixCityGraph = ox.graph_from_bbox(
                    north = northern_lat+0.1,
                    west = western_long-0.1,
                    south=southern_lat-0.1,
                    east = eastern_long+0.1,
                    network_type='drive',
                    simplify=False)

# impute missing edge speeds and calculate edge travel times with the speed module
phoenixCityGraph = ox.speed.add_edge_speeds(phoenixCityGraph)
phoenixCityGraph = ox.speed.add_edge_travel_times(phoenixCityGraph)

### Create Route

#### Using Nodes

In [6]:
# these are just the nodes closest to each coordinate
phoenixCityNodes = ox.distance.nearest_nodes(phoenixCityGraph,
                                             phoenixCityCoordsLongs,
                                             phoenixCityCoordsLats)

# this creates the list of nodes that make up the actual route in the graph
phoenixCityRoute = []
orig = phoenixCityNodes[0]
for dest in phoenixCityNodes[1:]:
    phoenixCityRoute = phoenixCityRoute[:-1] + nx.shortest_path(phoenixCityGraph, orig, dest, 'distance')
    orig = dest

#### Using Coordinates

In [7]:
# rewrote Karl's code for debugging, found that needed to add buffer to bounding box creation step
# phoenixCityOrig = ox.distance.nearest_nodes(phoenixCityGraph,
#                                             phoenixCityCoordsLongs[0],
#                                             phoenixCityCoordsLats[0])
# phoenixCityRoute = []
# for coord in phoenixCityCoords[1:]:
#       dest = ox.distance.nearest_nodes(phoenixCityGraph,
#                                        coord[1],
#                                        coord[0])
#       phoenixCityRoute = phoenixCityRoute[:-1] + \
#                          nx.shortest_path(phoenixCityGraph,
#                                           orig,
#                                           dest,
#                                           'distance')
#       orig = dest

### Folium Web Map with Folium

In [8]:
phoenix_route_map = ox.plot_route_folium(phoenixCityGraph, phoenixCityRoute, weight=1)
phoenix_route_map

## Google Elevation API + OSMnx Elevation and Grade

#### Get Elevation Data and Add to Graph

In [9]:
# add elevation to each of the nodes, using the google elevation API, then calculate edge grades
phoenixCityGraph = ox.elevation.add_node_elevations_google(phoenixCityGraph, api_key=google_elevation_api_key)
phoenixCityGraph = ox.elevation.add_edge_grades(phoenixCityGraph)

### Folium Route Node Elevation Web Map

#### No Layers

In [10]:
display(phoenixCityGraph.nodes[phoenixCityRoute[0]])
display(phoenixCityGraph.nodes[phoenixCityRoute[0]]['y'])

{'y': 33.4657523,
 'x': -112.0562266,
 'highway': 'crossing',
 'street_count': 2,
 'elevation': 335.144}

33.4657523

In [11]:
# display(phoenixCityRoute)

# set initial values min and max for node color map
min_route_node_elev = float('inf')
max_route_node_elev = float('-inf')

# get lat and long of each node and put it into popup for each node
for route_node in phoenixCityRoute:
    node_lat = phoenixCityGraph.nodes[route_node]['y']
    node_long = phoenixCityGraph.nodes[route_node]['x']
    node_elev = phoenixCityGraph.nodes[route_node]['elevation']

    # update min and max elevation values
    if node_elev < min_route_node_elev:
        min_route_node_elev = node_elev
    if node_elev > max_route_node_elev:
        max_elev = node_elev

    # Assign color based on elevation value
    if node_elev <= min_route_node_elev + (max_route_node_elev - min_route_node_elev) / 3:
        route_node_color = 'blue'
    elif node_elev <= min_route_node_elev + (max_route_node_elev - min_route_node_elev) * 2 / 3:
        route_node_color = 'yellow'
    else:
        route_node_color = 'red'

    route_node_popup = \
    f"""Lat: {str(node_lat)}
    Long: {str(node_long)}
    Node: {route_node}
    Elevation: {node_elev}"""
    folium.CircleMarker((node_lat, node_long),
                        radius=1,
                        color=route_node_color,
                        popup=route_node_popup
                        ).add_to(phoenix_route_map)
phoenix_route_map

#### Add Layers

In [12]:
layered_phoenix_route_map = ox.plot_route_folium(phoenixCityGraph, phoenixCityRoute, weight=1)
node_elevation_feature_group = folium.FeatureGroup('Node Elevation', show=False)


# set initial values min and max for node color map
min_route_node_elev = float('inf')
max_route_node_elev = float('-inf')

# get lat and long of each node and put it into popup for each node
for route_node in phoenixCityRoute:
    node_lat = phoenixCityGraph.nodes[route_node]['y']
    node_long = phoenixCityGraph.nodes[route_node]['x']
    node_elev = phoenixCityGraph.nodes[route_node]['elevation']

    # update min and max elevation values
    if node_elev < min_route_node_elev:
        min_route_node_elev = node_elev
    if node_elev > max_route_node_elev:
        max_route_node_elev = node_elev

    # Assign color based on elevation value
    if node_elev <= min_route_node_elev + (max_route_node_elev - min_route_node_elev) / 3:
        route_node_color = 'blue'
    elif node_elev <= min_route_node_elev + (max_route_node_elev - min_route_node_elev) * 2 / 3:
        route_node_color = 'yellow'
    else:
        route_node_color = 'red'

    route_node_popup = \
    f"""Lat: {str(node_lat)}
    Long: {str(node_long)}
    Node: {route_node}
    Elevation: {node_elev}"""
    folium.CircleMarker((node_lat, node_long),
                        radius=1,
                        color=route_node_color,
                        popup=route_node_popup
                        ).add_to(node_elevation_feature_group)
node_elevation_feature_group.add_to(layered_phoenix_route_map)
folium.LayerControl().add_to(layered_phoenix_route_map)
layered_phoenix_route_map

### Folium Route Edge Grade Web Map

#### Figure out how edges work

In [13]:
nodes_gdfs, edges_gdfs = ox.graph_to_gdfs(phoenixCityGraph)

In [14]:
display(nodes_gdfs.columns)
display(edges_gdfs.columns)

Index(['y', 'x', 'street_count', 'elevation', 'highway', 'ref', 'geometry'], dtype='object')

Index(['osmid', 'oneway', 'lanes', 'highway', 'reversed', 'length',
       'speed_kph', 'travel_time', 'grade', 'grade_abs', 'bridge', 'ref',
       'name', 'maxspeed', 'junction', 'tunnel', 'access', 'area', 'geometry'],
      dtype='object')

In [15]:
display(nodes_gdfs.head())
edges_gdfs = edges_gdfs.reset_index()
display(edges_gdfs)

y           x  street_count  elevation highway  ref  \
osmid                                                                   
13265445  33.413341 -112.013661             2    340.461     NaN  NaN   
13266035  33.387323 -111.962613             2    361.973     NaN  NaN   
13266043  33.387276 -111.961375             3    361.008     NaN  NaN   
13266047  33.386528 -111.958467             3    359.609     NaN  NaN   
13266053  33.385425 -111.953807             2    354.455     NaN  NaN   

                             geometry  
osmid                                  
13265445  POINT (-112.01366 33.41334)  
13266035  POINT (-111.96261 33.38732)  
13266043  POINT (-111.96138 33.38728)  
13266047  POINT (-111.95847 33.38653)  
13266053  POINT (-111.95381 33.38542)

u            v  key      osmid  oneway lanes        highway  \
0          13265445   6149095234    0  436948657    True     1  motorway_link   
1          13266035    256189699    0   28808945    True     1  motorway_link   
2          13266043   2291377636    0   23657872    True     4       motorway   
3          13266047    255734721    0  102320627    True     5       motorway   
4          13266053    255735872    0  528041712    True     6       motorway   
...             ...          ...  ...        ...     ...   ...            ...   
265717  10792571979  10792571982    0  436968099    True     3        primary   
265718  10792571982  10792571985    0  436968099    True     3        primary   
265719  10792571985   7980725311    0  436968099    True     3        primary   
265720  10792669947     41588126    0  512525892   False     5       tertiary   
265721  10792669947   5215737396    0  512525892   False     5       tertiary   

        reversed   length  speed_kph  ...  grade_abs  bridge    ref  \
0          False   31.248       76.9  ...      0.019     NaN    NaN   
1          False  119.081       76.9  ...      0.015     NaN    NaN   
2          False   39.938      104.6  ...      0.024     yes  US 60   
3          False  165.758      104.6  ...      0.003     NaN  US 60   
4          False  793.062      104.6  ...      0.006     NaN  US 60   
...          ...      ...        ...  ...        ...     ...    ...   
265717     False   17.285       62.5  ...      0.007     NaN    NaN   
265718     False   23.242       62.5  ...      0.004     NaN    NaN   
265719     False   78.875       62.5  ...      0.001     NaN    NaN   
265720     False   31.839       56.3  ...      0.002     NaN    NaN   
265721      True   10.390       56.3  ...      0.001     NaN    NaN   

                          name maxspeed junction tunnel access area  \
0                          NaN      NaN      NaN    NaN    NaN  NaN   
1                          NaN      NaN      NaN    NaN    NaN  NaN   
2         Superstition Freeway   65 mph      NaN    NaN    NaN  NaN   
3         Superstition Freeway   65 mph      NaN    NaN    NaN  NaN   
4         Superstition Freeway   65 mph      NaN    NaN    NaN  NaN   
...                        ...      ...      ...    ...    ...  ...   
265717  East Washington Street      NaN      NaN    NaN    NaN  NaN   
265718  East Washington Street      NaN      NaN    NaN    NaN  NaN   
265719  East Washington Street      NaN      NaN    NaN    NaN  NaN   
265720   East Roosevelt Street   35 mph      NaN    NaN    NaN  NaN   
265721   East Roosevelt Street   35 mph      NaN    NaN    NaN  NaN   

                                                 geometry  
0       LINESTRING (-112.01366 33.41334, -112.01346 33...  
1       LINESTRING (-111.96261 33.38732, -111.96134 33...  
2       LINESTRING (-111.96138 33.38728, -111.96095 33...  
3       LINESTRING (-111.95847 33.38653, -111.95682 33...  
4       LINESTRING (-111.95381 33.38542, -111.94527 33...  
...                                                   ...  
265717  LINESTRING (-112.03114 33.44832, -112.03132 33...  
265718  LINESTRING (-112.03132 33.44832, -112.03157 33...  
265719  LINESTRING (-112.03157 33.44832, -112.03242 33...  
265720  LINESTRING (-112.02949 33.45858, -112.02915 33...  
265721  LINESTRING (-112.02949 33.45858, -112.02960 33...  

[265722 rows x 22 columns]

'osmid', 'oneway', 'lanes', 'highway', 'reversed', 'length',
       'speed_kph', 'travel_time', 'grade', 'grade_abs', 'bridge', 'ref',
       'name', 'maxspeed', 'junction', 'tunnel', 'access', 'area', 'geometry'

In [16]:
# filter gdfs for just route
route_nodes_gdf = nodes_gdfs[nodes_gdfs.index.isin(phoenixCityRoute)]
display(route_nodes_gdf.head())

route_edges_gdf = edges_gdfs[edges_gdfs['u'].isin(phoenixCityRoute) & edges_gdfs['v'].isin(phoenixCityRoute)]
route_edges_gdf = edges_gdfs.drop(columns=['oneway', 'lanes', 'bridge', 'reversed',
       'speed_kph', 'travel_time','junction', 'tunnel', 'access', 'area', 'geometry'])
display(route_edges_gdf.head())


y           x  street_count  elevation            highway  \
osmid                                                                         
41246505  33.427265 -112.042839             3    338.310  motorway_junction   
41386832  33.427741 -112.047892             4    332.825    traffic_signals   
41477997  33.427248 -112.049273             2    337.620                NaN   
41478003  33.427802 -112.049666             3    332.428                NaN   
41499734  33.429214 -112.060836             3    332.988                NaN   

          ref                     geometry  
osmid                                       
41246505  194  POINT (-112.04284 33.42726)  
41386832  NaN  POINT (-112.04789 33.42774)  
41477997  NaN  POINT (-112.04927 33.42725)  
41478003  NaN  POINT (-112.04967 33.42780)  
41499734  NaN  POINT (-112.06084 33.42921)

u           v  key      osmid        highway   length  grade  \
0  13265445  6149095234    0  436948657  motorway_link   31.248  0.019   
1  13266035   256189699    0   28808945  motorway_link  119.081 -0.015   
2  13266043  2291377636    0   23657872       motorway   39.938 -0.024   
3  13266047   255734721    0  102320627       motorway  165.758  0.003   
4  13266053   255735872    0  528041712       motorway  793.062 -0.006   

   grade_abs    ref                  name maxspeed  
0      0.019    NaN                   NaN      NaN  
1      0.015    NaN                   NaN      NaN  
2      0.024  US 60  Superstition Freeway   65 mph  
3      0.003  US 60  Superstition Freeway   65 mph  
4      0.006  US 60  Superstition Freeway   65 mph

In [17]:
route_edge_attributes = ox.utils_graph.get_route_edge_attributes(phoenixCityGraph,
                                                                 phoenixCityRoute)

# get first edge
display(route_edge_attributes[0])
display(route_edge_attributes[0]['osmid'])

# # get first edge u and v from route_edges_gdf
# edge_result = route_edges_gdf.loc[route_edges_gdf['osmid'] == route_edge_attributes[0]['osmid']]
# display(edge_result)

# get first node, find the edge it is attached to?
first_node_result = route_edges_gdf.loc[route_edges_gdf['u'] == phoenixCityRoute[0]]
display(first_node_result)

second_node_result = route_edges_gdf.loc[route_edges_gdf['v'] == phoenixCityRoute[1]]
display(second_node_result)

first_edge = route_edges_gdf.loc[(route_edges_gdf['u'] == phoenixCityRoute[0]) &
                                 (route_edges_gdf['v'] == phoenixCityRoute[1])]
first_grade = first_edge['grade_abs'].iloc[0]
display(first_edge, first_grade)
print(f'first edge grade: {first_grade}')


{'osmid': 436955648,
 'oneway': False,
 'lanes': '7',
 'name': 'East McDowell Road',
 'highway': 'secondary',
 'maxspeed': '35 mph',
 'reversed': True,
 'length': 12.839,
 'speed_kph': 56.3,
 'travel_time': 0.8,
 'grade': -0.005,
 'grade_abs': 0.005}

436955648

u           v  key      osmid    highway  length  grade  \
155818  3736905403  3736905404    0  436955648  secondary  29.194  0.004   
155819  3736905403  2459943493    0  436955648  secondary  12.839 -0.005   

        grade_abs  ref                name maxspeed  
155818      0.004  NaN  East McDowell Road   35 mph  
155819      0.005  NaN  East McDowell Road   35 mph

u           v  key      osmid    highway  length  grade  \
124039  2265617501  2459943493    0  538934269   tertiary  14.935  0.000   
155819  3736905403  2459943493    0  436955648  secondary  12.839 -0.005   
160217  4146316221  2459943493    0  538934270   tertiary  13.488 -0.002   
160218  4146316222  2459943493    0  436955653  secondary  10.529  0.003   

        grade_abs  ref                name maxspeed  
124039      0.000  NaN   North 12th Street   30 mph  
155819      0.005  NaN  East McDowell Road   35 mph  
160217      0.002  NaN   North 12th Street      NaN  
160218      0.003  NaN  East McDowell Road   35 mph

u           v  key      osmid    highway  length  grade  \
155819  3736905403  2459943493    0  436955648  secondary  12.839 -0.005   

        grade_abs  ref                name maxspeed  
155819      0.005  NaN  East McDowell Road   35 mph

0.005

first edge grade: 0.005


In [18]:
orig = phoenixCityRoute[0]
for dest in phoenixCityRoute[1:]:
    edge = route_edges_gdf.loc[(route_edges_gdf['u'] == orig) &
                               (route_edges_gdf['v'] == dest)]
    edge_grade = edge['grade_abs'].iloc[0]
    orig_lat = phoenixCityGraph.nodes[orig]['y']
    orig_long = phoenixCityGraph.nodes[orig]['x']
    dest_lat = phoenixCityGraph.nodes[dest]['y']
    dest_long = phoenixCityGraph.nodes[dest]['x']
    edge_grade = edge['grade_abs']
    edge_locations = [(orig_lat, orig_long),
                      (dest_lat, dest_long)]
    route_edge_popup = \
    f"""Grade: {edge_grade}"""
    folium.PolyLine(edge_locations,
                    popup = route_edge_popup,
                    color = 'black',
                    weight = 1).add_to()
    orig = dest

TypeError: Element.add_to() missing 1 required positional argument: 'parent'

#### Make Folium Grade Map

In [ ]:
grade_phoenix_route_map = ox.plot_route_folium(phoenixCityGraph, phoenixCityRoute, weight=1)
node_elevation_feature_group = folium.FeatureGroup('Node Elevation', show=False)
edge_grade_feature_group = folium.FeatureGroup('Edge Grade', show=False)
edge_grade_filter_feature_group = folium.FeatureGroup('Edge Grade Filter', show=False)

# set initial values for min and max for grade color map
min_route_edge_grade = float('inf')
max_route_edge_grade = float('-inf')

# set grade filter value
grade_filter = 0.003

# loop to create colorlines, then add popup, then add color
orig = phoenixCityRoute[0]
for dest in phoenixCityRoute[1:]:
    edge = route_edges_gdf.loc[(route_edges_gdf['u'] == orig) &
                               (route_edges_gdf['v'] == dest)]
    edge_grade = edge['grade_abs'].iloc[0]
    orig_lat = phoenixCityGraph.nodes[orig]['y']
    orig_long = phoenixCityGraph.nodes[orig]['x']
    dest_lat = phoenixCityGraph.nodes[dest]['y']
    dest_long = phoenixCityGraph.nodes[dest]['x']

    # update min and max grade values
    if edge_grade < min_route_edge_grade:
        min_route_edge_grade = edge_grade
    if edge_grade > max_route_edge_grade:
        max_route_edge_grade = edge_grade

    # Assign color based on elevation value
    if edge_grade <= min_route_edge_grade + (max_route_edge_grade - min_route_edge_grade) / 3:
        route_edge_color = 'blue'
    elif edge_grade <= min_route_edge_grade + (max_route_edge_grade - min_route_edge_grade) * 2 / 3:
        route_edge_color = 'yellow'
    else:
        route_edge_color = 'red'

    # create color filter
    if edge_grade >= grade_filter:
        route_edge_color_filter = 'red'
    else:
        route_edge_color_filter = 'blue'

    edge_locations = [(orig_lat, orig_long),
                      (dest_lat, dest_long)]
    route_edge_popup = \
    f"""Grade: {edge_grade}"""
    folium.PolyLine(edge_locations,
                    popup = route_edge_popup,
                    color = route_edge_color,
                    weight = 5).add_to(edge_grade_feature_group)
    folium.PolyLine(edge_locations,
                    popup = route_edge_popup,
                    color = route_edge_color_filter,
                    weight = 5).add_to(edge_grade_filter_feature_group)
    orig = dest


# add feature groups and display folium map
node_elevation_feature_group.add_to(grade_phoenix_route_map)
edge_grade_feature_group.add_to(grade_phoenix_route_map)
edge_grade_filter_feature_group.add_to(grade_phoenix_route_map)
folium.LayerControl().add_to(grade_phoenix_route_map)
grade_phoenix_route_map

## Create Final Web Map For Checkpoint

Create all three feature groups at once and save this version as the html output.

In [ ]:
phoenix_route_final_web_map = ox.plot_route_folium(phoenixCityGraph, phoenixCityRoute, weight=1)
node_elevation_feature_group = folium.FeatureGroup('Node Elevation', show=False)
edge_grade_feature_group = folium.FeatureGroup('Edge Grade', show=False)
edge_grade_filter_feature_group = folium.FeatureGroup('Edge Grade Filter', show=False)

# set initial values min and max for node color map
min_route_node_elev = float('inf')
max_route_node_elev = float('-inf')

# get lat and long of each node and put it into popup for each node
for route_node in phoenixCityRoute:
    node_lat = phoenixCityGraph.nodes[route_node]['y']
    node_long = phoenixCityGraph.nodes[route_node]['x']
    node_elev = phoenixCityGraph.nodes[route_node]['elevation']

    # update min and max elevation values
    if node_elev < min_route_node_elev:
        min_route_node_elev = node_elev
    if node_elev > max_route_node_elev:
        max_route_node_elev = node_elev

    # Assign color based on elevation value
    if node_elev <= min_route_node_elev + (max_route_node_elev - min_route_node_elev) / 3:
        route_node_color = 'blue'
    elif node_elev <= min_route_node_elev + (max_route_node_elev - min_route_node_elev) * 2 / 3:
        route_node_color = 'yellow'
    else:
        route_node_color = 'red'

    route_node_popup = \
    f"""Lat: {str(node_lat)}
    Long: {str(node_long)}
    Node: {route_node}
    Elevation: {node_elev}"""
    folium.CircleMarker((node_lat, node_long),
                        radius=1,
                        color=route_node_color,
                        popup=route_node_popup
                        ).add_to(node_elevation_feature_group)

# set initial values for min and max for grade color map
min_route_edge_grade = float('inf')
max_route_edge_grade = float('-inf')

# set grade filter value
grade_filter = 0.003

# loop to create colorlines, then add popup, then add color
orig = phoenixCityRoute[0]
for dest in phoenixCityRoute[1:]:
    edge = route_edges_gdf.loc[(route_edges_gdf['u'] == orig) &
                               (route_edges_gdf['v'] == dest)]
    edge_grade = edge['grade_abs'].iloc[0]
    orig_lat = phoenixCityGraph.nodes[orig]['y']
    orig_long = phoenixCityGraph.nodes[orig]['x']
    dest_lat = phoenixCityGraph.nodes[dest]['y']
    dest_long = phoenixCityGraph.nodes[dest]['x']

    # update min and max grade values
    if edge_grade < min_route_edge_grade:
        min_route_edge_grade = edge_grade
    if edge_grade > max_route_edge_grade:
        max_route_edge_grade = edge_grade

    # Assign color based on elevation value
    if edge_grade <= min_route_edge_grade + (max_route_edge_grade - min_route_edge_grade) / 3:
        route_edge_color = 'blue'
    elif edge_grade <= min_route_edge_grade + (max_route_edge_grade - min_route_edge_grade) * 2 / 3:
        route_edge_color = 'yellow'
    else:
        route_edge_color = 'red'

    # create color filter
    if edge_grade >= grade_filter:
        route_edge_color_filter = 'red'
    else:
        route_edge_color_filter = 'blue'

    edge_locations = [(orig_lat, orig_long),
                      (dest_lat, dest_long)]
    route_edge_popup = \
    f"""Grade: {edge_grade}"""
    folium.PolyLine(edge_locations,
                    popup = route_edge_popup,
                    color = route_edge_color,
                    weight = 5).add_to(edge_grade_feature_group)
    folium.PolyLine(edge_locations,
                    popup = route_edge_popup,
                    color = route_edge_color_filter,
                    weight = 5).add_to(edge_grade_filter_feature_group)
    orig = dest

# add feature groups and display folium map
node_elevation_feature_group.add_to(phoenix_route_final_web_map)
edge_grade_feature_group.add_to(phoenix_route_final_web_map)
edge_grade_filter_feature_group.add_to(phoenix_route_final_web_map)
folium.LayerControl().add_to(phoenix_route_final_web_map)
phoenix_route_final_web_map
# output to html
# phoenix_route_final_web_map.save('phoenix_route_final_web_map.html')

# I-80 Route From Phillip
I-80 Sacramento to Soda Springs
- [https://goo.gl/maps/u9cJoNBq7nxJ4K7w6](https://goo.gl/maps/u9cJoNBq7nxJ4K7w6)

Functionality Flow:
- User creates route in browser using Google Maps
- __Import this route into this program somehow__
- Convert to coordinates
- __Get just elevation for this route, not entire graph__ (if there is time)
- Clean up Phoenix route code from above

Outline:
- Google API Key
- Get coordinates from Google API
- Create bounding box
- Create graph
- Create route
- Call Google Elevation API
- GeoPandas
- Folium


To Do:
- write up checkpoint document
    - find out if I need spend time making functions (doing this now is waste of time, just need to explain why)
- Google maps route to coordinates
- Get elevation data only for nodes on route
    - maybe there is a way to remove nodes not on the route before calling elevation api?
- Clean up node and edge work before folium map
- Make final submission notebook
- Documentation and any other write ups
- Demo presentation